In [3]:
from google.colab import files
files.upload()

Saving Benign_list_big_final.csv to Benign_list_big_final.csv


{'Benign_list_big_final.csv': b"http://1337x.to/torrent/1048648/American-Sniper-2014-MD-iTALiAN-DVDSCR-X264-BST-MT/\r\nhttp://1337x.to/torrent/1110018/Blackhat-2015-RUSSIAN-720p-WEB-DL-DD5-1-H264-RUFGT/\r\nhttp://1337x.to/torrent/1122940/Blackhat-2015-x264-1080p-WEB-DL-eng-nl-subs-sharky/\r\nhttp://1337x.to/torrent/1124395/Fast-and-Furious-7-2015-HD-TS-XVID-AC3-HQ-Hive-CM8/\r\nhttp://1337x.to/torrent/1145504/Avengers-Age-of-Ultron-2015-CAM-New-Audio-x264-CPG/\r\nhttp://1337x.to/torrent/1160078/Avengers-age-of-Ultron-2015-HQ-CAM-H264-AC3-MURD3R/\r\nhttp://1337x.to/torrent/294349/American-Idol-S11E04-Auditions-4-HDTV-XviD-FQM-ettv/\r\nhttp://189.cn/dqmh/userCenter/myOrderInfoList.do?method=listMyOrderInfo_new&isVs=no\r\nhttp://2gis.ru/moscow/search/%D0%9F%D0%BE%D0%B5%D1%81%D1%82%D1%8C/tab/firms/zoom/11\r\nhttp://abc.go.com/shows/general-hospital/episode-guide/2015-05/08-friday-may-8-2015\r\nhttp://abc.go.com/shows/the-muppets/video/new-abc-comedy-trailers?cid=abchp_muppets\r\nhttp://abcn

In [4]:
import pandas as pd
data = pd.read_csv("Benign_list_big_final.csv")
data.head()

http://1337x.to/torrent/1048648/American-Sniper-2014-MD-iTALiAN-DVDSCR-X264-BST-MT/
0  http://1337x.to/torrent/1110018/Blackhat-2015-...                                 
1  http://1337x.to/torrent/1122940/Blackhat-2015-...                                 
2  http://1337x.to/torrent/1124395/Fast-and-Furio...                                 
3  http://1337x.to/torrent/1145504/Avengers-Age-o...                                 
4  http://1337x.to/torrent/1160078/Avengers-age-o...

In [5]:
#collecting 1000 valid urls randomly for testing
data.columns = ['URLs']
valid_urls = data.head(200).copy()
valid_urls = valid_urls.reset_index(drop=True)
valid_urls.shape

(200, 1)

In [6]:
!pip uninstall whois
!pip install python-whois

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 109.6/109.6 kB 2.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for python-whois: filename=python_whois-0.8.0-py3-none-any.whl size=103247 sha256=9f21ba3fa93923abe4c0c17f523cee0f8465123dc5fdbaa6d8d042f28b4a7633
  Stored in directory: /root/.cache/pip/wheels/10/f1/87/145023b9a206e2e948be6480c61ef3fd3dbb81ef11b6977782
Successfully built python-whois


In [ ]:
import re
import whois
from datetime import datetime
import requests

def domain_age(url):
    try:
        # Extract the domain from the URL
        domain = url.split("//")[-1].split("/")[0]

        # Perform a WHOIS lookup to get domain information
        domain_info = whois.whois(domain)

        # Extract the creation date from the WHOIS data
        creation_date = domain_info.creation_date

        if isinstance(creation_date, list):
            creation_date = creation_date[0]

        # Calculate domain age
        if creation_date:
            today = datetime.now()
            age = (today - creation_date).days
            # if age of domain < 6 months
            if ((age/30) < 6):
              age = 1
            else:
              age = 0
            return age

    except Exception as e:
        #print("dang")
        return None

total = 2000
false_positive_count = 0
none_count = 0
for i in range(0, total//2):
  url = valid_urls['URLs'][i]
  age = domain_age(url)
  if age != None:
    false_positive_count += age
  else:
    none_count+=1
false_positive_count


Error trying to connect to socket: closing socket - timed out
Error trying to connect to socket: closing socket - [Errno -2] Name or service not known
Error trying to connect to socket: closing socket - [Errno -2] Name or service not known
Error trying to connect to socket: closing socket - [Errno -2] Name or service not known
Error trying to connect to socket: closing socket - [Errno -2] Name or service not known
Error trying to connect to socket: closing socket - [Errno -2] Name or service not known
Error trying to connect to socket: closing socket - [Errno -2] Name or service not known
Error trying to connect to socket: closing socket - [Errno -2] Name or service not known
Error trying to connect to socket: closing socket - timed out
Error trying to connect to socket: closing socket - timed out
Error trying to connect to socket: closing socket - timed out
Error trying to connect to socket: closing socket - timed out
Error trying to connect to socket: closing socket - timed out
Error

5

In [ ]:
none_count

103

In [ ]:
def url_length(url):
  if len(url) < 54:
      length = 0
  else:
      length = 1
  return length

total = 2000
false_positive_count = 0
for i in range(0, total//2):
  url = valid_urls['URLs'][i]
  l = url_length(url)
  false_positive_count += l

false_positive_count

1000

In [ ]:
def contains_ip_address(url):
    return int(bool(re.search(r'\d{1,3}\.\d{1,3}\.\d{1,3}\.\d{1,3}', url)))

total = 2000
t = 0
for i in range(0, total//2):
  url = valid_urls['URLs'][i]
  l = contains_ip_address(url)
  t += l

t

1

In [8]:
import re
import whois
from datetime import datetime
import requests

def has_ssl_certificate(url):
    try:
        response = requests.get(url)
        if response.status_code == 200:
            if response.url.startswith("https://"):
                return 0 # 0 for has ssl certificate
            else:
                return 1 # 1 for does not have ssl certificate - potential phishing
        else:
            print(f"HTTP request failed with status code: {response.status_code}")
            return None
    except requests.exceptions.RequestException as e:
        print(f"Request error: {e}")
        return None

total = 2000
false_positive_count = 0
none_count = 0
for i in range(0, 200):
  url = valid_urls['URLs'][i]
  age = has_ssl_certificate(url)
  if age != None:
    false_positive_count += age
  else:
    none_count+=1
false_positive_count

HTTP request failed with status code: 412
HTTP request failed with status code: 403
HTTP request failed with status code: 404
HTTP request failed with status code: 404
Request error: HTTPSConnectionPool(host='adultfriendfinder.com', port=443): Max retries exceeded with url: /css/live_cd/ffadult/english/0/font_face-1427390957.css (Caused by SSLError(SSLError(1, '[SSL: UNSAFE_LEGACY_RENEGOTIATION_DISABLED] unsafe legacy renegotiation disabled (_ssl.c:1007)')))
HTTP request failed with status code: 403
HTTP request failed with status code: 403
HTTP request failed with status code: 403
HTTP request failed with status code: 403
HTTP request failed with status code: 403
HTTP request failed with status code: 403
HTTP request failed with status code: 403
HTTP request failed with status code: 403
HTTP request failed with status code: 403
HTTP request failed with status code: 403
HTTP request failed with status code: 406
HTTP request failed with status code: 405
HTTP request failed with status c

115

In [10]:
none_count

85